# Ralstonia Annotation Tool

## Imports

In [15]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [16]:
from pathlib import Path
from io import StringIO
import json
from datetime import datetime as dt

import pandas as pd
import panel as pn

import scripts.tap_const as tc
import scripts.tap_image as ti

## Setup

In [17]:
pn.extension("tabulator")

template = pn.template.BootstrapTemplate(title="Ralstonia Annotation Tool")

In [18]:
pd.set_option("display.max_colwidth", 500)
pd.set_option("display.max_columns", 500)
pd.set_option("display.width", 1000)
pd.set_option("display.max_rows", 20)

## Constants

In [19]:
EXPERIMENT = "72AC_PhD_2404"

In [ ]:
INDEX_KEY = "date_time"

In [20]:
# Setup Paths
if tc.phenopsis.joinpath(EXPERIMENT).is_dir() is True:
    pt_data = tc.data
    pt_images = tc.phenopsis.joinpath(EXPERIMENT)
    pt_rotations = tc.dataout.joinpath("rotation_angles").joinpath(f"{EXPERIMENT}")
else:
    here = Path(".").parent
    pt_data = here.joinpath("data")
    pt_images = here.joinpath("images").joinpath(EXPERIMENT)
    pt_rotations = here.joinpath("rotation_angles").joinpath(f"{EXPERIMENT}")


In [21]:
treatments = {
    "Ralstonia": "RS",
    "Control": "CT",
    "Hydric Stress": "HS",
    "DC3000": "DC",
}

In [35]:
# pd.read_csv(pt_data.joinpath(f"{EXPERIMENT}_raw.csv"), sep=";").assign(date_time=lambda x: x.date_time.str.split(".", expand=True)[0])

experiment             plant              camera            date_time  angle wavelength  height  job_id                                                              filepath      robot        date             time  hour  plant_id PositionPlante  plaque  position treatment   x   y                         timestamp                                                             file_name
0     72AC_PhD_2404   72AC73_CL_RS_XX  cam_scan_phenopsis  2024-07-27 10:06:09      0      SW755       0    2273   72AC_PhD_2404#20240727120609#72AC73_CL_RS_XX#LIN#0#SW755#2273#0.tif  phenopsis  2024-07-27  10:06:09.601000    12        73          P3_A1       3         1        RS  13   1  2024-07-27 10:06:09.601000+00:00   72AC_PhD_2404#20240727120609#72AC73_CL_RS_XX#LIN#0#SW755#2273#0.jpg
1     72AC_PhD_2404   72AC73_CL_RS_XX  cam_scan_phenopsis  2024-07-27 13:06:10      0      SW755       0    2274   72AC_PhD_2404#20240727150610#72AC73_CL_RS_XX#LIN#0#SW755#2274#0.tif  phenopsis  2024-07-27  13:06:10.811000    15        73          P3_A1       3         1        RS  13   1  2024-07-27 13:06:10.811000+00:00   72AC_PhD_2404#20240727150610#72AC73_CL_RS_XX#LIN#0#SW755#2274#0.jpg
2     72AC_PhD_2404   72AC73_CL_RS_XX  cam_scan_phenopsis  2024-07-28 10:06:11      0      SW755       0    2277   72AC_PhD_2404#20240728120610#72AC73_CL_RS_XX#LIN#0#SW755#2277#0.tif  phenopsis  2024-07-28  10:06:11.133000    12        73          P3_A1       3         1        RS  13   1  2024-07-28 10:06:11.133000+00:00   72AC_PhD_2404#20240728120610#72AC73_CL_RS_XX#LIN#0#SW755#2277#0.jpg
3     72AC_PhD_2404   72AC73_CL_RS_XX  cam_scan_phenopsis  2024-07-28 13:06:12      0      SW755       0    2278   72AC_PhD_2404#20240728150612#72AC73_CL_RS_XX#LIN#0#SW755#2278#0.tif  phenopsis  2024-07-28  13:06:12.678000    15        73          P3_A1       3         1        RS  13   1  2024-07-28 13:06:12.678000+00:00   72AC_PhD_2404#20240728150612#72AC73_CL_RS_XX#LIN#0#SW755#2278#0.jpg
4     72AC_PhD_2404   72AC73_CL_RS_XX  cam_scan_phenopsis  2024-07-29 10:06:10      0      SW755       0    2281   72AC_PhD_2404#20240729120609#72AC73_CL_RS_XX#LIN#0#SW755#2281#0.tif  phenopsis  2024-07-29  10:06:10.204000    12        73          P3_A1       3         1        RS  13   1  2024-07-29 10:06:10.204000+00:00   72AC_PhD_2404#20240729120609#72AC73_CL_RS_XX#LIN#0#SW755#2281#0.jpg
...             ...               ...                 ...                  ...    ...        ...     ...     ...                                                                   ...        ...         ...              ...   ...       ...            ...     ...       ...       ...  ..  ..                               ...                                                                   ...
6043  72AC_PhD_2404  72AC468_CL_DC_XX  cam_scan_phenopsis  2024-08-05 10:37:34      0      SW755       0    2310  72AC_PhD_2404#20240805123734#72AC468_CL_DC_XX#LIN#0#SW755#2310#0.tif  phenopsis  2024-08-05  10:37:34.721000    12       468        P13_A36      13        36        DC  36  12  2024-08-05 10:37:34.721000+00:00  72AC_PhD_2404#20240805123734#72AC468_CL_DC_XX#LIN#0#SW755#2310#0.jpg
6044  72AC_PhD_2404  72AC468_CL_DC_XX  cam_scan_phenopsis  2024-08-05 13:37:35      0      SW755       0    2311  72AC_PhD_2404#20240805153734#72AC468_CL_DC_XX#LIN#0#SW755#2311#0.tif  phenopsis  2024-08-05  13:37:35.100000    15       468        P13_A36      13        36        DC  36  12  2024-08-05 13:37:35.100000+00:00  72AC_PhD_2404#20240805153734#72AC468_CL_DC_XX#LIN#0#SW755#2311#0.jpg
6045  72AC_PhD_2404  72AC468_CL_DC_XX  cam_scan_phenopsis  2024-08-06 10:37:30      0      SW755       0    2314  72AC_PhD_2404#20240806123730#72AC468_CL_DC_XX#LIN#0#SW755#2314#0.tif  phenopsis  2024-08-06  10:37:30.918000    12       468        P13_A36      13        36        DC  36  12  2024-08-06 10:37:30.918000+00:00  72AC_PhD_2404#20240806123730#72AC468_CL_DC_XX#LIN#0#SW755#2314#0.jpg
6046  72AC_PhD_2404  72AC468_CL_DC_XX  cam_scan_phenopsis  2024-08-06

## User Interface

### Widgets

In [30]:
dwn_template = pn.widgets.FileDownload(
    file=pt_data.joinpath(f"{EXPERIMENT}_raw.csv"),
    filename=f"{EXPERIMENT}_raw.csv",
    button_type="success",
    label="Download template annotation file",
    sizing_mode="stretch_width",
)

file_input = pn.widgets.FileInput(accept=".csv,.json", sizing_mode="stretch_width")
table = pn.widgets.Tabulator(
    value=pd.DataFrame(),
    pagination="local",
    page_size=20,
    sizing_mode="stretch_width",
)


sl_treatment = pn.widgets.Select(
    name="Treatment", options=list(treatments.keys()), value="Ralstonia"
)
sl_plant = pn.widgets.Select(name="Plant", options=[])
ck_show_finished = pn.widgets.Checkbox(name="Show completed plants", value=False)

im_current = pn.pane.Image(max_width=800, max_height=800, sizing_mode="stretch_width")
discrete_slider = pn.widgets.DiscreteSlider(
    name="Discrete Player", options=[0], value=0
)
bt_previous = pn.widgets.ButtonIcon(icon="caret-left", size="4em", toggle_duration=500)
bt_next = pn.widgets.ButtonIcon(icon="caret-right", size="4em", toggle_duration=500)
ii_disease_index = pn.widgets.IntInput(
    name="Disease Index",
    start=0,
    end=4,
    step=1,
    value=0,
    max_width=80,
    sizing_mode="stretch_width",
)

dwn_annotations = pn.widgets.FileDownload(
    file=pt_data.joinpath(f"{EXPERIMENT}_raw.csv"),
    filename=f"{EXPERIMENT}_raw.csv",
    label="Download",
    name="Download Annotations",
    sizing_mode="stretch_width",
    icon="file-download",
    button_type="primary",
)
pg_completion = pn.indicators.Progress(name="Annotation progress", value=0)

### Callbacks

In [27]:
updating: bool = False


@pn.depends(file_input.param.value, watch=True)
def on_file_loaded(value):
    if not value or not isinstance(value, bytes):
        return pd.DataFrame()

    string_io = StringIO(value.decode("utf8"))
    ret = pd.read_csv(string_io, sep=";").assign(
        file_name=lambda x: x.filepath.str.replace(".tif", ".jpg"),
        date_time=lambda x: x.date_time.str.split(".", expand=True)[0],
    )
    if "di" not in ret:
        ret["di"] = 0
    if "done" not in ret:
        ret["done"] = False

    table.value = ret


@pn.depends(
    table.param.value,
    ck_show_finished.param.value,
    sl_treatment.param.value,
    watch=True,
)
def on_table_changed(file: str, show_done: bool, treatment):
    df = table.value
    if "done" in df and "treatment" in df:
        df = df[df.treatment == treatments[treatment]]
        sl_plant.options = list(
            df.plant.unique()
            if show_done is True
            else df[df.done == False].plant.unique()
        )


@pn.cache(max_items=10, policy="LRU")
def get_plant_data(df, plant_name) -> pd.DataFrame:
    file_names, rotations = [], []
    for k, v in json.load(
        open(pt_rotations.joinpath(sl_plant.value).with_suffix(".json"), "r")
    ).items():
        file_names.append(k + ".jpg")
        rotations.append(v)

    return df[df.plant == plant_name].merge(
        pd.DataFrame(data={"file_name": file_names, "rotation": rotations}),
        on="file_name",
        how="left",
    )


def update_image():
    global updating
    updating = True
    try:
        row = (
            get_plant_data(df=table.value, plant_name=sl_plant.value)
            .set_index(INDEX_KEY)
            .loc[discrete_slider.value]
        )
        if pt_images.joinpath(row.file_name).is_file() is True:
            im_current.object = ti.to_pil(
                ti.rotate_image(
                    image=ti.load_image(file_name=row.file_name, file_path=pt_images),
                    angle=row.rotation,
                )
            )
            ii_disease_index.value = row.di
        else:
            im_current.object = None
    finally:
        updating = False


@pn.depends(sl_plant.param.value, watch=True)
def on_plant_changed(plant_name):
    discrete_slider.options = get_plant_data(df=table.value, plant_name=plant_name)[
        INDEX_KEY
    ].to_list()
    discrete_slider.value = discrete_slider.options[0]
    update_image()


@pn.depends(discrete_slider.param.value, watch=True)
def on_index_changed(index):
    update_image()


def do_previous(event):
    discrete_slider.value = discrete_slider.options[
        max(discrete_slider.options.index(discrete_slider.value) - 1, 0)
    ]


def do_next(event):
    discrete_slider.value = discrete_slider.options[
        min(
            discrete_slider.options.index(discrete_slider.value) + 1,
            len(discrete_slider.options) - 1,
        )
    ]


bt_previous.on_click(do_previous)
bt_next.on_click(do_next)


@pn.depends(ii_disease_index.param.value, watch=True)
def on_di_changed(di):
    if updating is True:
        return
    table.value.loc[
        (table.value.plant == sl_plant.value)
        & (table.value[INDEX_KEY] >= discrete_slider.value),
        "di",
    ] = di
    table.value.loc[(table.value.plant == sl_plant.value), "done"] = True

    s_buf = StringIO()
    table.value.to_csv(s_buf, sep=";")
    s_buf.seek(0)
    dwn_annotations.filename = f"{EXPERIMENT}_{dt.now().strftime('%Y%d%m_%H%M%S')}.csv"
    dwn_annotations.file = s_buf
    dwn_annotations.visible = True

    pg_completion.max = len(table.value.plant.unique())
    pg_completion.value = len(table.value[table.value.done == True].plant.unique())

In [32]:
a = [1, 2, 3, 4, 5, 6]
a.index(3)

2

### Build Components

In [28]:
sidebar = pn.Column(
    pn.Card(
        pn.Column(
            pn.pane.Markdown("**Step 1:** Doawload the annaotation template file."),
            pn.pane.Alert(
                """Only download the template the first time, changes are stored on your computer only.""",
                alert_type="danger",
            ),
            dwn_template,
            pn.pane.Markdown("**Step 2:** Uplaod the downloaded template file."),
            file_input,
            pn.pane.Markdown(
                """**Step 3:** Annotate images. 
                Uppon finishing or before closing the app us the download button next to the disease index selector to download the annotations."""
            ),
            pn.pane.Alert(
                "If you want to resume an existing annotation session, upload your latest download.",
                alert_type="info",
            ),
        ),
        title="File Manager",
    ),
    pn.WidgetBox(
        "#### Plant selection",
        sl_treatment,
        sl_plant,
        ck_show_finished,
        sizing_mode="stretch_width",
    ),
    pn.WidgetBox(
        "#### Annotation progress", pg_completion, sizing_mode="stretch_width"
    ),
)
main = pn.Column(
    im_current,
    pn.Row(bt_previous, discrete_slider, bt_next, ii_disease_index, dwn_annotations),
    max_width=800,
    max_height=800,
    sizing_mode="stretch_width",
)

### Test

In [29]:
# sidebar.width = 330
pn.Row(sidebar, main)

BokehModel(combine_events=True, render_bundle={'docs_json': {'fbfa3e7d-2cea-465d-9844-cecbf0c4a154': {'version…

## Render

In [ ]:
template.sidebar.append(sidebar)
template.main.append(main)
template.servable()